In [1]:
## La version de python utilisée est 3.12.7

!pip install -r requirements.txt -q

In [2]:
import pandas as pd
import lxml as lxml
import io as io
import geopandas as gpd
import pandas as pd
import geopandas as gpd

from script import mapping

In [3]:
# Charger le fichier SHP
gdf = gpd.read_file('data/zones_inondables/zones_inondables.shp')

C:\Users\flori\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\pyogrio\raw.py:198: RuntimeWarning: data/zones_inondables/zones_inondables.shp contains polygon(s) with rings with invalid winding order. Autocorrecting them, but that shapefile should be corrected using ogr2ogr for example.
  return ogr_read(


Les zones inondables sont localisées en système Lambert-93 (coordonnées planes, EPSG 2154)

In [4]:
print(gdf.crs)

EPSG:2154


On les convertit dans le système GPS longitude/latitude (WGS 84, EPSG 4326)

In [5]:
gdf.to_crs(4326, inplace=True)

In [6]:
base = pd.read_parquet('data/transactions_with_zone_inondable.parquet')

In [7]:
# Étape 1 : Lister les noms des communes ayant au moins une "submersion marine"
communes_submersion = base.loc[base['libelle_type_inondation'] == "submersion marine", 'nom_commune'].unique()

# Étape 2 : Filtrer le DataFrame pour ne garder que :
# - Les communes ayant une submersion marine
# - Les communes où "identifiant_tri" est renseigné pour au moins une des lignes
base = base[
    base['nom_commune'].isin(communes_submersion) & 
    base.groupby('nom_commune')['identifiant_tri'].transform('any')
]

In [8]:
# Supprimer les doublons par 'nom_commune'
commune = base.drop_duplicates(subset='nom_commune')

# Retenir uniquement les colonnes 'nom_commune' et 'Population'
commune = commune[['nom_commune', 'Population']]

# Trier par 'Population' de manière décroissante
commune = commune.sort_values(by='Population', ascending=False)

In [9]:
# Filtrer les valeurs uniques par 'nom_commune' et trier par 'population'
top_100_communes = base.drop_duplicates(subset='nom_commune').nlargest(100, 'Population')

# Afficher un aperçu des 40 plus grandes communes
display(top_100_communes[['nom_commune', 'Population']])


nom_commune  Population
8185                      Nice      348085
51978                 Bordeaux      261804
120229                  Toulon      180452
25617                     Caen      108200
91509                Dunkerque       86788
...                        ...         ...
33707   Saint-Georges-d'Oléron        3948
15                      Fleury        3896
123518        Beauvoir-sur-Mer        3876
38871                  Bénodet        3790
30831                   Arvert        3774

[100 rows x 2 columns]

In [10]:
# Filtrer 'base' pour ne conserver que les communes présentes dans 'top_100_communes'
top_100_communes_names = top_100_communes['nom_commune'].unique()  # Liste des noms de communes les plus peuplées
filtered_base = base[base['nom_commune'].isin(top_100_communes_names)]

# Grouper par 'nom_commune' et 'identifiant_tri', puis compter le nombre d'occurrences
zone_counts = filtered_base.groupby(['nom_commune', 'identifiant_tri']).size().reset_index(name='nombre_occurences')

# Ajouter la population des communes à 'zone_counts' en fusionnant avec 'top_100_communes'
zone_counts = pd.merge(zone_counts, top_100_communes[['nom_commune', 'Population']], on='nom_commune', how='left')

# Trier par population des communes (en ordre décroissant)
tri_by_commune = zone_counts.sort_values(by='Population', ascending=False) \
    .drop(columns=['Population']) \
.reset_index(drop=True)

# Afficher le résultat trié
display(tri_by_commune)

nom_commune                         identifiant_tri  \
0                      Nice                            FRD_TRI_NICE   
1                  Bordeaux                            FRF_TRI_BORD   
2                    Toulon                          FRD_TRI_TOULON   
3                      Caen                            FRH_TRI_CAEN   
4                 Dunkerque                       FRA_TRI_DUNKERQUE   
..                      ...                                     ...   
96   Saint-Georges-d'Oléron            FRFG_TRI_LITTORAL_CHARENTAIS   
97                   Fleury                        FRD_TRI_NARBONNE   
98         Beauvoir-sur-Mer    FRG_TRI_NOIRMOUTIER_ST_JEAN_DE_MONTS   
99                  Bénodet  FRG_TRI_QUIMPER_LITTORAL_SUD_FINISTERE   
100                  Arvert            FRFG_TRI_LITTORAL_CHARENTAIS   

     nombre_occurences  
0                  985  
1                  330  
2                  633  
3                   39  
4                  129  
..                 ...  
96                  13  
97                  71  
98                  19  
99                  13  
100                  1  

[101 rows x 3 columns]

In [11]:
tri_by_commune

nom_commune                         identifiant_tri  \
0                      Nice                            FRD_TRI_NICE   
1                  Bordeaux                            FRF_TRI_BORD   
2                    Toulon                          FRD_TRI_TOULON   
3                      Caen                            FRH_TRI_CAEN   
4                 Dunkerque                       FRA_TRI_DUNKERQUE   
..                      ...                                     ...   
96   Saint-Georges-d'Oléron            FRFG_TRI_LITTORAL_CHARENTAIS   
97                   Fleury                        FRD_TRI_NARBONNE   
98         Beauvoir-sur-Mer    FRG_TRI_NOIRMOUTIER_ST_JEAN_DE_MONTS   
99                  Bénodet  FRG_TRI_QUIMPER_LITTORAL_SUD_FINISTERE   
100                  Arvert            FRFG_TRI_LITTORAL_CHARENTAIS   

     nombre_occurences  
0                  985  
1                  330  
2                  633  
3                   39  
4                  129  
..                 ...  
96                  13  
97                  71  
98                  19  
99                  13  
100                  1  

[101 rows x 3 columns]

In [12]:
gdf = gdf.drop(columns=['id','dept'])

In [13]:
# Forcer la conversion de la colonne 'beach_coordinates' en liste de tuples (latitude, longitude)
base['beach_coordinates'] = base['beach_coordinates'].apply(mapping.force_convert_to_tuple_list)
base['station'] = base['station'].apply(mapping.force_convert_to_tuple_list)


In [14]:
communes_coordinates = (
    base[['nom_commune',                         
          'latitude_mairie',
          'longitude_mairie',
          'latitude_port',
          'longitude_port',
          'station',
          'beach_coordinates',
          'Population']]
    .drop_duplicates(subset=['nom_commune'], keep='first')  # Supprime les doublons sur 'nom_commune', garde le premier
    .merge(
        tri_by_commune.drop(columns=['nombre_occurences']),  # Retire 'nombre_occurences' avant la jointure
        how='left',
        on='nom_commune'
    )
    .sort_values(by='Population',ascending=False)  # Trie par ordre alphabétique sur 'nom_commune'
)

In [15]:
# mapping.generate_and_save_maps(base, communes_coordinates, gdf)

Un exemple : à Cherbourg-en-Cotentin, le gradient de prix est dirigé autour du port et de la mairie. Les zones inondables ont des prix moyens beaucoup plus faibles

In [22]:
mapping.display_map_in_notebook('Cherbourg-en-Cotentin', base, communes_coordinates, gdf, zoom=13,latitude_add=+0.01,longitude_add=-0.01)

Lorsque la zone inondable est plus large, le gradient de prix est perturbé, mais s'éloigne de la zone.

A Ouistreham, la zone inondable (lié au ruissellement du fleuve) coupe la ville en 2. Le gradient négatif vers cette zone puis positif au delà.

In [17]:
mapping.display_map_in_notebook('Ouistreham', base, communes_coordinates, gdf, zoom=13,latitude_add=0.0,longitude_add=0.00)


A Andernos, les gradients sont très forts auprès des différentes plages, mais deviennent négatifs sur le reste du littoral, qui est inondable.

In [18]:
mapping.display_map_in_notebook('Andernos-les-Bains', base, communes_coordinates, gdf, zoom=13,latitude_add=-0.02,longitude_add=-0.01)


A Agde, le gradient est très fort vers la plage de la Dalle, mais devient négatif aussitôt qu'on s'en éloigne et qu'on se rapproche des zones inondables

In [19]:
mapping.display_map_in_notebook('Cannes', base, communes_coordinates, gdf, zoom=14, latitude_add=-0.0, longitude_add=0.0)